In [1]:
import numpy as np
import torch
import matplotlib.pyplot as plt
from PIL import Image
import os
import json
import pandas as pd
from src.utils.GAM_testing_utility import *

In [2]:
root_path = './output/GANs/'
classes = np.load(root_path + 'classes.npy')

model_class_acc = np.load(root_path + 'model_class_acc.npy')
model_pred = np.load(root_path + 'model_predictions.npy')

train_idx = np.load(root_path + 'train_index.npy')
test_idx = np.load(root_path + 'test_index.npy')
val_idx = np.load(root_path + 'val_index.npy')

# only get directories
model_names = [ f for f in os.listdir(root_path) if os.path.isdir(os.path.join(root_path, f)) ]
model_names.sort() 


model_df = pd.DataFrame(np.array(model_names), columns=['model'])
pd.set_option('display.max_columns', None)
model_df

model
0  current_best_v1
1             name

In [3]:
selected_model = 0


# 'all', 'train', 'test', 'val
data_subset = 'all'

In [4]:
name = model_names[selected_model]
model_path = root_path + name + '/' + name

with open(model_path + '_config.json') as json_file: 
    config = json.load(json_file)

generator, encoder, model, dataloader = setup_nets(model_path, config)
latent_aug = get_aug_function(config['latent_aug_name'])

if not os.path.exists(model_path + '_latent.npy'):
    pred, latents = calc_preds_latents(generator, encoder, model, dataloader, latent_aug)
    np.save(model_path + '_pred.npy', pred.numpy())
    np.save(model_path + '_latent.npy', latents.numpy())

latents = np.load(model_path + '_latent.npy')
pred = np.load(model_path + '_pred.npy')

if not os.path.exists(model_path + '_mean_std.npy'):
    mean_latent = np.mean(latents, 0)
    std_latent = np.std(latents, 0)
    np.save(model_path + '_mean_std.npy', np.vstack([mean_latent,std_latent]))
mean_std = np.load(model_path + '_mean_std.npy')

In [ ]:
class_latents, class_pred, class_correct = separate(classes, pred, latents)

In [ ]:
classes_sub, pred_sub, latents_sub = use_dataset(data_subset, train_idx, test_idx, val_idx, classes, pred, latents)
class_acc = calc_class_acc(classes_sub, pred_sub)
class_rank = np.argsort(class_acc)

# Testing

In [ ]:
print(f'mean accuracy of subset {data_subset} : {np.mean(class_acc)}')

mean accuracy of subset all : 0.9523965529063652


In [ ]:
rank_data = np.vstack((class_rank.astype(np.int64), class_acc[class_rank]))
rank_df = pd.DataFrame(rank_data, index=['class', 'acc'])
pd.set_option('display.max_columns', None)
rank_df

0           1          2           3          4         5    \
class  55.000000  129.000000  183.00000  106.000000  74.000000  3.000000   
acc     0.761905    0.793103    0.80198    0.818182   0.833333  0.835821   

             6          7          8          9          10          11   \
class  87.000000  26.000000  33.000000  27.000000  75.000000  150.000000   
acc     0.836364   0.841463   0.846154   0.846154   0.846154    0.846154   

             12         13         14        15          16          17   \
class  24.000000  39.000000  37.000000  5.000000  143.000000  105.000000   
acc     0.847458   0.849315   0.865385  0.867347    0.870968    0.873016   

          18          19         20          21          22          23   \
class  49.000  154.000000  89.000000  127.000000  195.000000  160.000000   
acc     0.875    0.877551   0.882353    0.884615    0.891304    0.894737   

              24          25    26     27          28       29         30   \
class  177.000000  119.000000  57.0  194.0  165.000000  6.00000  137.00000   
acc      0.895349    0.897959   0.9    0.9    0.903226  0.90566    0.90625   

              31         32          33          34         35         36   \
class  138.000000  67.000000  122.000000  135.000000  19.000000  43.000000   
acc      0.909091   0.909091    0.909091    0.910714   0.913043   0.914894   

             37         38         39          40         41         42   \
class  29.000000  73.000000  40.000000  139.000000  98.000000  28.000000   
acc     0.915094   0.916667   0.916667    0.918033   0.918919   0.918919   

          43      44          45       46         47         48         49   \
class  193.00  102.00  130.000000  7.00000  44.000000  78.000000  56.000000   
acc      0.92    0.92    0.921569  0.92233   0.923077   0.925926   0.925926   

              50          51         52          53         54          55   \
class  116.000000  110.000000  10.000000  117.000000  51.000000  155.000000   
acc      0.926829    0.926829   0.927536    0.928571   0.929577    0.930556   

              56          57          58        59        60       61   \
class  172.000000  142.000000  178.000000  126.0000  191.0000  72.0000   
acc      0.934066    0.934783    0.936709    0.9375    0.9375   0.9375   

           62       63          64          65          66          67   \
class  15.0000  91.0000  182.000000  171.000000  157.000000  180.000000   
acc     0.9375   0.9375    0.938272    0.941176    0.941176    0.941176   

             68          69         70         71          72        73   \
class  31.000000  114.000000  88.000000  35.000000  145.000000  47.00000   
acc     0.942529    0.944444   0.945946   0.945946    0.947368   0.94958   

         74        75          76       77         78          79         80   \
class  94.00  81.00000  123.000000  107.000  48.000000  170.000000  128.00000   
acc     0.95   0.95122    0.951613    0.952   0.952096    0.952381    0.95302   

             81         82          83         84          85        86   \
class  85.000000  36.000000  164.000000  14.000000  175.000000  46.00000   
acc     0.953368   0.954545    0.955056   0.956522    0.958015   0.95858   

             87     88     89     90          91         92        93   \
class  92.000000  76.00  32.00  42.00  196.000000  59.000000  0.000000   
acc     0.958848   0.96   0.96   0.96    0.960784   0.960784  0.961538   

             94         95          96          97          98         99   \
class  38.000000  23.000000  185.000000  152.000000  149.000000  25.000000   
acc     0.961538   0.961538    0.962963    0.963415    0.963636   0.964286   

              100         101        102        103        104       105  \
class  186.000000  184.000000  54.000000  99.000000  16.000000  13.00000   
acc      0.964286    0.965517   0.965517   0.967033   0.967742   0.96875   

              106         107         108        109         110         111  \
clas

In [ ]:
acc_vs_model(class_acc, model_class_acc)

In [ ]:
con_matrix = confusion_matrix(class_pred)

fig, ax = plt.subplots(1,1,figsize=(10,10))
fig.set_facecolor('white')
ax.imshow(con_matrix, cmap='gray')
ax.set_ylabel('real class')
ax.set_xlabel('predicted class')
ax.set_title('Confusion matrix')


Text(0.5, 1.0, 'Confusion matrix')

In [ ]:
visual_insection(generator, encoder, model)

/home/thorreign/anaconda3/lib/python3.8/site-packages/torch/nn/functional.py:718: UserWarning: Named tensors and all their associated APIs are an experimental feature and subject to change. Please do not use them for anything important until they are released as stable. (Triggered internally at  /opt/conda/conda-bld/pytorch_1623448278899/work/c10/core/TensorImpl.h:1156.)
  return torch.max_pool2d(input, kernel_size, stride, padding, dilation, ceil_mode)


[  0  21  48  94 153]


In [ ]:
show_class(class_latents, class_pred, 21, 0, generator)